# Project Report

In [14]:
import pandas as pd
import ta
import plotly.graph_objects as go
import requests
from io import StringIO
import numpy as np
import optuna
import matplotlib.image as mpimg
import matplotlib.pyplot as plt

In [15]:
url = "https://raw.githubusercontent.com/Rerris/Technical_Analysis_Proyect/main/data/aapl_1h_test.csv"

response = requests.get(url, verify=True)
data = pd.read_csv(StringIO(response.text))

# %%
#RSI
rsi_indicator = ta.momentum.RSIIndicator(close=data['Close'], window=14)
data['RSI'] = rsi_indicator.rsi()
#MACD
macd_indicator = ta.trend.MACD(close=data['Close'], window_slow=26, window_fast=12, window_sign=9)
data['macd'] = macd_indicator.macd()
data['macd_signal'] = macd_indicator.macd_signal()

# Crear instancia del indicador EMA con períodos de 13 y 48
ema_13_indicator = ta.trend.EMAIndicator(close=data['Close'], window=13)
ema_48_indicator = ta.trend.EMAIndicator(close=data['Close'], window=48)
    
# Calcular las EMAs 13 y 48 
data['Ema 13'] = ema_13_indicator.ema_indicator()
data['Ema 48'] = ema_48_indicator.ema_indicator()
# Inicializar el indicador EMA con una ventana de 200 períodos
ema_indicator = ta.trend.EMAIndicator(close=data['Close'], window=200)
# Calcular la EMA 200

data['Ema 200'] = ema_indicator.ema_indicator()

# %%
def rsi_long(data, window):
    rsi_indicator = ta.momentum.RSIIndicator(close=data['Close'], window= window)
    data['RSI'] = rsi_indicator.rsi()
    data["RSI_TF_Long"]=False
    
    for i in range(len(data)):
        # Obtener el valor actual de RSI
        rsi_value = data['RSI'].iloc[i]

        # Si el valor de RSI es mayor que 50, establecer "True" en la columna "RSI_TF"
        if rsi_value > 50:
            data["RSI_TF_Long"].iloc[i] = True

    return data
            

# %%
window = 14

# %%
rsi_long(data,window)

# %%
def rsi_short(data, window):
    rsi_indicator = ta.momentum.RSIIndicator(close=data['Close'], window=window)
    data['RSI'] = rsi_indicator.rsi()
    data["RSI_TF_Short"]=False
    
    for i in range(len(data)):
        # Obtener el valor actual de RSI
        rsi_value = data['RSI'].iloc[i]

        # Si el valor de RSI es mayor que 50, establecer "True" en la columna "RSI_TF"
        if rsi_value > 50:
            data["RSI_TF_Short"].iloc[i] = True

    return data

# %%
window = 14

# %%
rsi_short(data,window)

# %%
def macd_long(data, window_slow, window_fast, window_sign):
    macd_indicator = ta.trend.MACD(close=data['Close'], window_slow = window_sign, window_fast = window_fast, window_sign = window_sign)
    data['macd'] = macd_indicator.macd()
    data['macd_signal'] = macd_indicator.macd_signal()

    # Últimos valores de MACD y señal
    macd = data['macd']
    macd_signal = data['macd_signal']

    data["MACD_TF"] = False

    for i in range(1, len(data)):
        # Si el MACD cruza hacia arriba la línea de señal en este punto de datos
        if macd.iloc[i] > macd_signal.iloc[i] and macd.iloc[i - 1] <= macd_signal.iloc[i - 1]:
            data["MACD_TF"].iloc[i] = True

    return data

# %%
window_slow = 26
window_fast = 12
window_sign = 9

# %%
macd_long(data, window_slow, window_fast, window_sign)

# %%
def macd_short(data, window_slow, window_fast, window_sign):
    macd_indicator = ta.trend.MACD(close=data['Close'], window_slow = window_sign, window_fast = window_fast, window_sign = window_sign)
    data['macd'] = macd_indicator.macd()
    data['macd_signal'] = macd_indicator.macd_signal()

    # Últimos valores de MACD y señal
    macd = data['macd']
    macd_signal = data['macd_signal']

    data["MACD_TF_Short"] = False

    for i in range(1, len(data)):
        # Si el MACD cruza hacia arriba la línea de señal en este punto de datos
        if macd.iloc[i] < macd_signal.iloc[i] and macd.iloc[i - 1] <= macd_signal.iloc[i - 1]:
            data["MACD_TF_Short"].iloc[i] = True

    return data

# %%
macd_short(data, window_slow, window_fast, window_sign)

# %%
def ema_cross_long(data, ema_13_window, ema_48_window):
    # Crear instancia del indicador EMA con períodos de 13 y 48
    ema_13_indicator = ta.trend.EMAIndicator(close=data['Close'], window=ema_13_window)
    ema_48_indicator = ta.trend.EMAIndicator(close=data['Close'], window=ema_48_window)
    
    # Calcular las EMAs
    ema_13 = ema_13_indicator.ema_indicator()
    ema_48 = ema_48_indicator.ema_indicator()

    # Inicializar la señal de cruce a False
    data["EMA_cross_TF_Long"] = False

    # Iterar sobre los índices desde el segundo valor
    for i in range(1, len(data)):
        # Si hay un cruce alcista de la EMA de 13 sobre la EMA de 48
        """
        El siguiente codigo es por si se quiere hacer con con la compra al hacer el cruce unicamente cuando sucede
        if data['Ema 13'].iloc[i] > data['Ema 48'].iloc[i] and data['Ema 13'].iloc[i - 1] <= data['Ema 48'].iloc[i - 1] and not data["EMA_cross_TF_Long"].iloc[i - 1]:

        """
        if data['Ema 13'].iloc[i] > data['Ema 48'].iloc[i] and data['Ema 13'].iloc[i - 1] <= data['Ema 48'].iloc[i - 1]:
            data["EMA_cross_TF_Long"].iloc[i] = True

    return data

# %%
ema_13_window = 13
ema_48_window = 48

# %%
ema_cross_long(data, ema_13_window, ema_48_window)

# %%
def ema_cross_short(data, ema_13_window, ema_48_window):
    # Crear instancia del indicador EMA con períodos de 13 y 48
    ema_13_indicator = ta.trend.EMAIndicator(close=data['Close'], window=ema_13_window)
    ema_48_indicator = ta.trend.EMAIndicator(close=data['Close'], window=ema_48_window)
    
    # Calcular las EMAs
    ema_13 = ema_13_indicator.ema_indicator()
    ema_48 = ema_48_indicator.ema_indicator()

    # Inicializar la señal de cruce a False
    data["EMA_cross_TF_Short"] = False

    # Iterar sobre los índices desde el segundo valor
    for i in range(1, len(data)):
        """
        El siguiente codigo es por si se quiere hacer con con la compra al hacer el cruce unicamente cuando sucede
        
         if data['Ema 13'].iloc[i] < data['Ema 48'].iloc[i] and data['Ema 13'].iloc[i - 1] >= data['Ema 48'].iloc[i - 1] and not data["EMA_cross_TF_Short"].iloc[i - 1]:
        """
        # Si hay un cruce alcista de la EMA de 13 sobre la EMA de 48
        if data['Ema 13'].iloc[i] > data['Ema 48'].iloc[i] and data['Ema 13'].iloc[i - 1] <= data['Ema 48'].iloc[i - 1]:
            data["EMA_cross_TF_Short"].iloc[i] = True

    return data

# %%
ema_cross_short(data, ema_13_window, ema_48_window)

# %%
def ema_200_long(data, ema_200_window):
    # Inicializar el indicador EMA con una ventana de 200 períodos
    ema_indicator = ta.trend.EMAIndicator(close=data['Close'], window = ema_200_window)
    
    # Calcular la EMA
    ema_200 = ema_indicator.ema_indicator()
    
    # Inicializar la columna de señal de compra
    data["Ema 200 TF Long"] = False

    # Iterar sobre los índices desde el primer valor
    for i in range(len(data)):
        # Obtener el valor actual de la EMA de 200
        ema_200_value = data["Ema 200"].iloc[i]

        # Obtener el último precio de cierre
        ultimo_precio_cierre = data['Close'].iloc[i]

        # Si el precio está por encima de la EMA de 200, establecer la señal de compra en True
        if ultimo_precio_cierre > ema_200_value:
            data.at[i, "Ema 200 TF Long"] = True

    return data

# %%
def ema_200_short(data, ema_200_window):
    # Inicializar el indicador EMA con una ventana de 200 períodos
    ema_indicator = ta.trend.EMAIndicator(close=data['Close'], window=ema_200_window)
    
    # Calcular la EMA
    ema_200 = ema_indicator.ema_indicator()
    
    # Inicializar la columna de señal de compra
    data["Ema 200 TF Short"] = False

    # Iterar sobre los índices desde el primer valor
    for i in range(len(data)):
        # Obtener el valor actual de la EMA de 200
        ema_200_value = data["Ema 200"].iloc[i]

        # Obtener el último precio de cierre
        ultimo_precio_cierre = data['Close'].iloc[i]

        # Si el precio está por encima de la EMA de 200, establecer la señal de compra en True
        if ultimo_precio_cierre < ema_200_value:
            data.at[i, "Ema 200 TF Short"] = True

    return data

# %%
ema_200_window = 200

# %%
ema_200_long(data, ema_200_window)

# %%
ema_200_short(data, ema_200_window)

C:\Users\esteb\AppData\Local\Temp\ipykernel_17152\2151089473.py:40: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data["RSI_TF_Long"].iloc[i] = True
C:\Users\esteb\AppData\Local\Temp\ipykernel_17152\2151089473.py:40: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data["RSI_TF_Long"].iloc[i] = True
C:\Users\esteb\AppData\Local\Temp\ipykernel_17152\2151089473.py:40: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data["RSI_TF_Long"].iloc[i]

Timestamp  Gmtoffset             Datetime        Open        High   
0     1609770600          0  2021-01-04 14:30:00  133.570007  133.611602  \
1     1609774200          0  2021-01-04 15:30:00  131.054992  131.309997   
2     1609777800          0  2021-01-04 16:30:00  129.889892  130.089996   
3     1609781400          0  2021-01-04 17:30:00  128.246902  129.110000   
4     1609785000          0  2021-01-04 18:30:00  129.039993  129.199996   
...          ...        ...                  ...         ...         ...   
5728  1703871000          0  2023-12-29 17:30:00  191.904998  192.229995   
5729  1703874600          0  2023-12-29 18:30:00  191.904998  192.449996   
5730  1703878200          0  2023-12-29 19:30:00  192.115005  192.729995   
5731  1703881800          0  2023-12-29 20:30:00  192.675003  193.130004   
5732  1703883600          0  2023-12-29 21:00:00  192.529998  192.529998   

             Low       Close      Volume        RSI      macd  ...   
0     130.380004  131.053604  27653145.0        NaN       NaN  ...  \
1     129.399993  129.895004  20134055.0        NaN       NaN  ...   
2     126.760002  128.250000  23694210.0        NaN       NaN  ...   
3     127.630096  129.039794  14745063.0        NaN       NaN  ...   
4     128.595001  128.960006  10861778.0        NaN       NaN  ...   
...          ...         ...         ...        ...       ...  ...   
5728  191.779998  191.899993   3916853.0  34.181871  0.135557  ...   
5729  191.899993  192.119995   2809737.0  37.346632  0.145226  ...   
5730  192.110000  192.679992   4109754.0  44.643073  0.121456  ...   
5731  192.020004  192.520004   7753795.0  43.098820  0.109013  ...   
5732  192.529998  192.529998         NaN  43.230923  0.096774  ...   

          Ema 48     Ema 200  RSI_TF_Long  RSI_TF_Short  MACD_TF   
0            NaN         NaN        False         False    False  \
1            NaN         NaN        False         False    False   
2            NaN         NaN        False         False    False   
3            NaN         NaN        False         False    False   
4            NaN         NaN        False         False    False   
...          ...         ...          ...           ...      ...   
5728  193.732711  192.395314        False         False    False   
5729  193.666886  192.392574        False         False    False   
5730  193.626605  192.395434        False         False    False   
5731  193.581438  192.396674        False         False    False   
5732  193.538522  192.398000        False         False    False   

      MACD_TF_Short  EMA_cross_TF_Long  EMA_cross_TF_Short  Ema 200 TF Long   
0             False              False               False            False  \
1             False              False               False            False   
2             False              False               False            False   
3             False              False               False            False   
4             False              False               False            False   
...             ...                ...                 ...              ...   
5728          False              False               False            False   
5729          False              False               False            False   
5730          False              False               False             True   
5731          False              False               False             True   
5732          False              False               False             True   

      Ema 200 TF Short  
0                False  
1                False  
2                False  
3                False  
4                False  
...                ...  
5728              True  
5729              True  
5730             False  
5731             False  
5732             False  

[5733 rows x 22 columns]

In [16]:
def simular_operaciones_long_short(data, combinacion_bits):
    profit_total = 0
    estado = None  # 'long', 'short', None
    precio_entrada = 0

    for i in range(len(data)):
        # Determinar la acción basada en la combinación de bits
        # Señales para largos
        accion_long = (combinacion_bits & 1 and data['RSI_TF_Long'].iloc[i]) or \
                      (combinacion_bits & 2 and data['MACD_TF'].iloc[i]) or \
                      (combinacion_bits & 4 and data['EMA_cross_TF_Long'].iloc[i]) or \
                      (combinacion_bits & 8 and data['Ema 200 TF Long'].iloc[i])
        
        # Señales para cortos 
        accion_short = (combinacion_bits & 1 and data['RSI_TF_Short'].iloc[i]) or \
                       (combinacion_bits & 2 and data['MACD_TF_Short'].iloc[i]) or \
                       (combinacion_bits & 4 and data['EMA_cross_TF_Short'].iloc[i]) or \
                       (combinacion_bits & 8 and data['Ema 200 TF Short'].iloc[i])

        # Lógica combinada
        if accion_long and not accion_short and estado != 'long':
            if estado == 'short':  # Cerrar posición corta
                profit_total += precio_entrada - data['Close'].iloc[i]
            precio_entrada = data['Close'].iloc[i]
            estado = 'long'
        elif accion_short and not accion_long and estado != 'short':
            if estado == 'long':  # Cerrar posición larga
                profit_total += data['Close'].iloc[i] - precio_entrada
            precio_entrada = data['Close'].iloc[i]
            estado = 'short'

    # Cerrar cualquier posición abierta al final
    if estado == 'long':
        profit_total += data['Close'].iloc[-1] - precio_entrada
    elif estado == 'short':
        profit_total += precio_entrada - data['Close'].iloc[-1]

    return profit_total



def backtest_optimized(data, capital, take_profit_pct=None, stop_loss_pct=None):
    # Apply the indicator functions to the data
    data = rsi_long(data, window)
    data = macd_long(data, window_slow, window_fast, window_sign)
    data = ema_cross_long(data, ema_13_window, ema_48_window)
    data = ema_200_long(data, ema_200_window)
    data = rsi_short(data, window)
    data = macd_short(data, window_slow, window_fast, window_sign)
    data = ema_cross_short(data, ema_13_window, ema_48_window)
    data = ema_200_short(data, ema_200_window)

    # Obtener la mejor combinación de bits
    profits = [simular_operaciones_long_short(data, combinacion_bits) for combinacion_bits in range(16)]
    max_profit_index = profits.index(max(profits))
    mejor_combinacion_bits = "{:04b}".format(max_profit_index)

    # Inicializar columnas para señales de compra, venta y compra a corto
    data["Buy_Signal"] = False
    data["Sell_Signal"] = False
    data["Short_Sell_Signal"] = False

    # Inicializar lista para registrar cambios en el capital con el capital inicial
    capital_history = [capital]  

    # Iterar sobre los índices
    for i in range(len(data)):
        operar = False

        # Verificar si algún modelo activo da señal de compra o venta corta según la mejor combinación de bits
        if mejor_combinacion_bits[0] == '1' and data['RSI_TF_Long'].iloc[i]:
            operar = True
            data.at[i, "Buy_Signal"] = True
        if mejor_combinacion_bits[1] == '0' and data['MACD_TF'].iloc[i]:
            operar = True
            data.at[i, "Buy_Signal"] = True
        if mejor_combinacion_bits[2] == '0' and data['EMA_cross_TF_Long'].iloc[i]:
            operar = True
            data.at[i, "Buy_Signal"] = True
        if mejor_combinacion_bits[3] == '1' and data['Ema 200 TF Long'].iloc[i]:
            operar = True
            data.at[i, "Buy_Signal"] = True

        if mejor_combinacion_bits[0] == '1' and data['RSI_TF_Short'].iloc[i]:
            operar = True
            data.at[i, "Short_Sell_Signal"] = True
        if mejor_combinacion_bits[1] == '1' and data['MACD_TF_Short'].iloc[i]:
            operar = True
            data.at[i, "Short_Sell_Signal"] = True
        if mejor_combinacion_bits[2] == '1' and data['EMA_cross_TF_Short'].iloc[i]:
            operar = True
            data.at[i, "Short_Sell_Signal"] = True
        if mejor_combinacion_bits[3] == '1' and data['Ema 200 TF Short'].iloc[i]:
            operar = True
            data.at[i, "Short_Sell_Signal"] = True

        # Verificar si hay capital suficiente para realizar la operación
        if capital <= 0:
            operar = False

        # Verificar si hay que aplicar take profit o stop loss
        if operar:
            if take_profit_pct and data['Close'].iloc[i] >= data['Close'].iloc[i-1] * (1 + take_profit_pct):
                operar = False
                data.at[i, "Sell_Signal"] = True  # Generar señal de venta
            if stop_loss_pct and data['Close'].iloc[i] <= data['Close'].iloc[i-1] * (1 - stop_loss_pct):
                operar = False

        # Actualizar el capital según las operaciones
        if operar:
            # Calcular el monto a comprar
            amount_to_buy = min(capital * 0.0001, capital)
            capital -= amount_to_buy
        else:
            # Calcular el monto a vender si se cierra una posición
            amount_to_sell = amount_to_buy if data['Buy_Signal'].iloc[i] or data['Short_Sell_Signal'].iloc[i] else 0
            capital += amount_to_sell
            amount_to_buy = 0  # Reiniciar el monto a comprar

        # Actualizar el valor de capital_history
        capital_history.append(capital)

    # Agregar columna para el historial del capital al dataframe
    data["Capital"] = capital_history[:-1]  # Guardar el historial de capital en el dataframe

    # Convertir columnas booleanas a enteros
    buy_signal_int = data["Buy_Signal"].astype(int)
    sell_signal_int = data["Sell_Signal"].astype(int)
    short_sell_signal_int = data["Short_Sell_Signal"].astype(int)

    # Calcular el valor del portafolio (capital + valor actual de todas las acciones en posesión)
    valor_portafolio = capital + ((data["Close"] * buy_signal_int) - (data["Close"] * sell_signal_int) - (data["Close"] * short_sell_signal_int)).sum()
    
    # Agregar el valor final del portafolio al historial
    capital_history.append(valor_portafolio)

    return capital, valor_portafolio, data


In [17]:
import locale

# Set the locale to the appropriate currency format
locale.setlocale(locale.LC_ALL, 'en_US.UTF-8')

# Ejecutar la función backtest_optimized para obtener el historial del capital
take_profit_pct = 0.05
stop_loss_pct = 0.01
capital = 1000000
capital, valor_portafolio, data = backtest_optimized(data, capital)

# Obtener capital_history de los datos generados por backtest_optimized
capital_history = data["Capital"].tolist()

# Formatear el valor del portafolio
formatted_valor_portafolio = locale.currency(valor_portafolio, grouping=True)

# Imprimir el valor del portafolio
print(f"Profit using the optimized strategy: {formatted_valor_portafolio}")


C:\Users\esteb\AppData\Local\Temp\ipykernel_17152\2151089473.py:40: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data["RSI_TF_Long"].iloc[i] = True
C:\Users\esteb\AppData\Local\Temp\ipykernel_17152\2151089473.py:40: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data["RSI_TF_Long"].iloc[i] = True
C:\Users\esteb\AppData\Local\Temp\ipykernel_17152\2151089473.py:40: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data["RSI_TF_Long"].iloc[i]

C:\Users\esteb\AppData\Local\Temp\ipykernel_17152\2151089473.py:40: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data["RSI_TF_Long"].iloc[i] = True
C:\Users\esteb\AppData\Local\Temp\ipykernel_17152\2151089473.py:40: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data["RSI_TF_Long"].iloc[i] = True
C:\Users\esteb\AppData\Local\Temp\ipykernel_17152\2151089473.py:40: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data["RSI_TF_Long"].iloc[i]

Profit using the optimized strategy: $741,255.51


## Conclusiones
Nos percatamos de diferentes estrategias para comprar acciones y obtener ganancias. Aprendimos a utilizar diferentes indicadores para tomar decisiones de compra y venta, y a utilizar herramientas para analizar el comportamiento de las acciones. 
También vimos como es posible utilizar diferentes estrategias para obtener ganancias en el mercado de valores y esto gracias a la estrategia de los bits que utilizamos en el proyecto.

Al utilizar los diferentes files para testear la estrategia obtuvimos los siguientes resultados:
- 1 día = $1,002,975.42 de ganancia y esto debido a que casi no se hicieron compras
- 1 hr = $741,255.51 de ganancia y esto debido a que se hicieron más compras y ventas
- 5 min = -$1,082,737,63 de perdida y esto debido a que se hicieron muchas compras y ventas
- 1 min = 

Llegamos a la conclusión que nuestro bot esta diseñado para hacer pocas compras y ventas, por lo que es mejor utilizarlo en periodos de tiempo más largos, como 1 día o 1 hr.